<a href="https://colab.research.google.com/github/mathew1046/encide-ml-mathew/blob/main/animalClassification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import files
files.upload()

Saving test_images.zip to test_images.zip
Saving kaggle.json to kaggle.json


{'test_images.zip': b'PK\x03\x04\x14\x00\x00\x00\x00\x00`\r\xa9Z\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0c\x00\x00\x00test_images/PK\x03\x04\x14\x00\x00\x00\x08\x00\xf3\x9b\xa8ZS.\x83A\xc6\xd3\x00\x00N\xd4\x00\x00\x18\x00\x00\x00test_images/test_003.jpg\x9c[UT\x9cM\x93\x1e\x18\x1c\x82Cp\x1d\\\x82\xbb\xbb\xcb\xe0\x96\xe02Hp\r\x1eH\x98\xc0\xc0\xe0\xee\xee.\x01\xbe\x0cA\x06\x87\xe0\xc1\x82\x13<A\x83f\xf9\xf7\xac\xdc\xec\xc5\xee\xd6{\xd9}\xfa\xbcOwWu\xd5SU\x7f\x97\xfen\x00\x085T\xd4U\x00((\x00\x00\xca\xf3\x07\xf8\xbb\x02P\x04\xe0`bbab\xe0`aa\xe1\xe2\xe0\xe0\xe2S\x10\xe2\xbfx\x81OKFND\xc1L\xcf\x02b\xa2gbd\xe5\x12}\xc5\xca!\xc4\xc1\xc8\xc4\'\xcf/$.)##\xc3\xc2\xab\xa4\xae(\xa5&*-#\xf9\xafEPppq\xf1_\xe0\xd3\x10\x12\xd2H\xb23\xb1K\xfe\x9f\xe5/\x02@\x84\x85r\x81r\x00Da\x02\xa0\x12\xa1\x00\x89P\xfe\x0e\x00\xe8\x9f\xff\x13\x1d\xe5\xdf\x05\xf0\x1f\x82\x82\nDC\xc7\xc0\xc4\xc2\xc6\xc1}\x9e\xd0F\x08@E\x01\x02Q\xd1\x80\xe8\xe8hh\xcf\xa3\xa1\xcf\xe3\x004"tbF~y\x0c\x12}\x1bL&/R\x81Hx\x11\x16\xb

In [2]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [3]:
!kaggle datasets download -d aleemaparakatta/cats-and-dogs-mini-dataset

Dataset URL: https://www.kaggle.com/datasets/aleemaparakatta/cats-and-dogs-mini-dataset
License(s): unknown


In [4]:
! unzip -q cats-and-dogs-mini-dataset.zip

In [5]:
!mkdir -p data/Cat
!mkdir -p data/Dog

!mv cats_set/* data/Cat/
!mv dogs_set/* data/Dog/

In [6]:
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import os, shutil, random
import numpy as np
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import load_model
import pandas as pd
data_dir = 'data'
img_size = 160
batch_size = 32


In [7]:
train_gen = ImageDataGenerator(
    rescale=1./255,
    validation_split=0.2,
    horizontal_flip=True,
    rotation_range=20,
    zoom_range=0.2
)

train_data = train_gen.flow_from_directory(
    data_dir,
    target_size=(img_size, img_size),
    batch_size=batch_size,
    class_mode='binary',
    subset='training'
)

val_data = train_gen.flow_from_directory(
    data_dir,
    target_size=(img_size, img_size),
    batch_size=batch_size,
    class_mode='binary',
    subset='validation'
)


Found 800 images belonging to 2 classes.
Found 200 images belonging to 2 classes.


In [8]:
!rm -rf data/.ipynb_checkpoints

In [9]:
base_model = tf.keras.applications.MobileNetV2(
    input_shape=(img_size, img_size, 3),
    include_top=False,
    weights='imagenet'
)
base_model.trainable = False

9406464/9406464 ━━━━━━━━━━━━━━━━━━━━ 0s 0us/step


In [10]:
model = tf.keras.Sequential([
    base_model,
    tf.keras.layers.GlobalAveragePooling2D(),
    tf.keras.layers.Dense(1, activation='sigmoid')
])

In [11]:
model.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)

history = model.fit(
    train_data,
    validation_data=val_data,
    epochs=5
)

/usr/local/lib/python3.11/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


Epoch 1/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 37s 1s/step - accuracy: 0.8103 - loss: 0.4376 - val_accuracy: 0.8950 - val_loss: 0.2770
Epoch 2/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 27s 1s/step - accuracy: 0.9399 - loss: 0.1734 - val_accuracy: 0.9150 - val_loss: 0.2081
Epoch 3/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 27s 1s/step - accuracy: 0.9608 - loss: 0.1203 - val_accuracy: 0.9100 - val_loss: 0.2078
Epoch 4/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 27s 1s/step - accuracy: 0.9606 - loss: 0.1038 - val_accuracy: 0.9400 - val_loss: 0.1722
Epoch 5/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 28s 1s/step - accuracy: 0.9706 - loss: 0.0899 - val_accuracy: 0.9450 - val_loss: 0.1457


In [12]:
model.save('model.h5')

In [13]:
acc = history.history['accuracy']
print(f"Final Training Accuracy: {acc[-1]:.4f}")

Final Training Accuracy: 0.9737


In [14]:
!unzip -q test_images.zip

In [15]:
test_dir = 'test_images'
img_size = (160, 160)
for filename in sorted(os.listdir(test_dir)):
    if filename.lower().endswith(('.jpg', '.png', '.jpeg')):
        img_path = os.path.join(test_dir, filename)
        img = image.load_img(img_path, target_size=img_size)
        img_array = image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0) / 255.0  # Normalize

        pred = model.predict(img_array)[0][0]
        label = "Dog" if pred > 0.5 else "Cat"
        print(f"{filename}: {label} (Confidence: {pred:.4f})")


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
test_003.jpg: Dog (Confidence: 0.9683)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 107ms/step
test_005.jpg: Cat (Confidence: 0.0044)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 117ms/step
test_025.jpg: Dog (Confidence: 0.9993)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 108ms/step
test_030.jpg: Dog (Confidence: 0.9777)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step
test_039.jpg: Dog (Confidence: 0.9956)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
test_047.jpg: Dog (Confidence: 0.9875)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 90ms/step
test_050.jpg: Dog (Confidence: 0.9548)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
test_051.jpg: Dog (Confidence: 0.9968)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 85ms/step
test_054.jpg: Dog (Confidence: 0.9867)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step
test_055.jpg: Dog (Confidence: 0.9938)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 138ms/step
test_056.jpg: Dog (Confidence: 0.9992)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step
test_059.jpg: Cat (Confidence: 0.0054)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step
test_061.jpg: Dog (Confidence: 0.9